## Explainable Boosting Machine (一般化加法モデル) による解釈性の高いモデル開発
製造プロセスから採取されたセンサーデータと検査結果のデータを用いて、品質管理モデルを構築します。[interpretml - interpret](https://github.com/interpretml/interpret) に含まれる一般化加法モデルの推定アルゴリズム Explainable Boosting Machine を用います。

### 1. データ準備
データを Pandas DataFrame としてインポートします。

In [1]:
import pandas as pd
from sklearn.model_selection import train_test_split

# 製造工程のサンプルのダミーデータ
df = pd.read_csv("../data/Factory.csv")

In [2]:
df.head()

ID  Quality  ProcessA-Pressure  ProcessA-Humidity  ProcessA-Vibration  \
0   1        0                7.0               0.27                0.36   
1   2        0                6.3               0.30                0.34   
2   3        0                8.1               0.28                0.40   
3   4        0                7.2               0.23                0.32   
4   5        0                7.2               0.23                0.32   

   ProcessB-Light  ProcessB-Skill  ProcessB-Temp  ProcessB-Rotation  \
0            20.7           0.045           45.0              170.0   
1             1.6           0.049           14.0              132.0   
2             6.9           0.050           30.0               97.0   
3             8.5           0.058           47.0              186.0   
4             8.5           0.058           47.0              186.0   

   ProcessC-Density  ProcessC-PH  ProcessC-skewness  ProcessC-Time  
0            1.0010         3.00               0.45            8.8  
1            0.9940         3.30               0.49            9.5  
2            0.9951         3.26               0.44           10.1  
3            0.9956         3.19               0.40            9.9  
4            0.9956         3.19               0.40            9.9

In [3]:
from sklearn.model_selection import train_test_split

# 説明変数の選択
X = df.drop(columns=["Quality","ID"],axis=1)

# 目的変数の選択
y = df["Quality"].values

# 学習データとテストデータに分割
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.1, random_state=100, stratify=y)

### 2. データ探索
InterpreML にはデータの可視化のためのメソッドも組み込まれています。

In [4]:
from interpret import show
from interpret.data import ClassHistogram

hist = ClassHistogram().explain_data(X_train, y_train, name = 'Train Data')
show(hist)

/anaconda/envs/rai-demo/lib/python3.6/site-packages/interpret/provider/visualize.py:44: UserWarning: Cloud environment detected (['azureml', 'ipython-zmq', 'ipython']): viz integration is still experimental.
  detected_envs


### 3. Explainable Boosting Machine (EBM) によるモデル学習
解釈性の高い EBM アルゴリズムによって一般化加法モデルの推定を行います。交互作用項を考慮したいときは `interactions` で組み合わせ数や列インデックス番号の組み合わせを指定します。

In [5]:
from interpret.glassbox import ExplainableBoostingClassifier, LogisticRegression, ClassificationTree, DecisionListClassifier
seed = 1234
ebm = ExplainableBoostingClassifier(random_state=seed, interactions=4)
ebm.fit(X_train, y_train)   #Works on dataframes and numpy arrays

ExplainableBoostingClassifier(feature_names=['ProcessA-Pressure',
                                             'ProcessA-Humidity',
                                             'ProcessA-Vibration',
                                             'ProcessB-Light', 'ProcessB-Skill',
                                             'ProcessB-Temp',
                                             'ProcessB-Rotation',
                                             'ProcessC-Density', 'ProcessC-PH',
                                             'ProcessC-skewness',
                                             'ProcessC-Time',
                                             'ProcessA-Humidity x '
                                             'ProcessC-Time',
                                             'ProcessA-Humidity x '
                                             'ProcessC-Density',
                                             'ProcessB-Temp x '
                                             'ProcessC-sk

### 4. モデル解釈 (グローバル)
モデルの重要度と各説明変数や交互作用項の予測値に対する寄与度のグラフを表示します。

In [6]:
ebm_global = ebm.explain_global(name='EBM')
show(ebm_global)

### 5. モデル解釈 (ローカル)
学習済みの EBM モデルから算出されたテストデータの個々の予測値の解釈を行います。

In [7]:
# 例として、テストデータの冒頭 20 個のデータを対象
ebm_local = ebm.explain_local(X_test[:20], y_test[:20], name='EBM')
show(ebm_local)

###  6. EBM モデルの精度確認
モデル精度を ROC で確認します。

In [8]:
from interpret.perf import ROC

ebm_perf = ROC(ebm.predict_proba).explain_perf(X_test, y_test, name='EBM')
show(ebm_perf)

### 7. ロジスティック回帰、決定木モデルの学習

In [9]:
from interpret.glassbox import LogisticRegression, ClassificationTree

X_enc = pd.get_dummies(X, prefix_sep='.')
feature_names = list(X_enc.columns)
X_train_enc, X_test_enc, y_train, y_test = train_test_split(X_enc, y, test_size=0.20, random_state=seed)

lr = LogisticRegression(random_state=seed, feature_names=feature_names, penalty='l2')
lr.fit(X_train_enc, y_train)

tree = ClassificationTree()
tree.fit(X_train_enc, y_train)

/anaconda/envs/rai-demo/lib/python3.6/site-packages/sklearn/linear_model/_logistic.py:765: ConvergenceWarning:

lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression



### 8. ダッシュボードでのモデル比較

In [10]:
lr_perf = ROC(lr.predict_proba).explain_perf(X_test_enc, y_test, name='Logistic Regression')
tree_perf = ROC(tree.predict_proba).explain_perf(X_test_enc, y_test, name='Classification Tree')

show(lr_perf)
show(tree_perf)
show(ebm_perf)

### 9. モデル解釈の比較 (グローバル、ローカル)

#### Global Explain

In [11]:
lr_global = lr.explain_global(name='LR')
tree_global = tree.explain_global(name='Tree')

show(lr_global)
show(tree_global)
show(ebm_global)

#### Local Explain

In [12]:
lr_local = lr.explain_local(X_test[:20], y_test[:20], name='LR')
tree_local = tree.explain_local(X_test[:20], y_test[:20], name='Tree')

show(lr_local)
show(tree_local)
show(ebm_local)

#### ダッシュボード

In [13]:
# EBM、ロジスティック回帰、決定木の比較を行うダッシュボード
show([hist, lr_global, lr_local, lr_perf, tree_global, tree_local, tree_perf, ebm_global, ebm_local, ebm_perf], share_tables=True)